In [1]:
# load FSA geojson
import geopandas as gpd

gdf = gpd.read_file('gdf_poly.geojson')

In [2]:
ont = gdf.copy()
ont['first'] = [i[0] for i in ont['id']]
ont = ont[ont['first'].isin(["K", "L", "M", "N", "O", "P"])]
ont = ont.drop(columns = 'first')

In [31]:
from recipes.categorical_anomaly import CategoricalAnomalyDetector
detector = CategoricalAnomalyDetector(ont, metrics_column='Win Rate', 
                                        category_column='id', model_type='IsolationForest', 
                                        geotif_path='earth_pop/GHS_POP_E2015_GLOBE_R2019A_4326_30ss_V1_0.tif',
                                        ScalerClass="StandardScaler",)

In [32]:
pop = detector.raster_to_vector()

In [33]:
pop.head()

id    bids  impressions  clicks       spend  Win Rate       CTR  \
2   K1B     249          237       0    2.759268  0.951807  0.000000   
6   K0J   45535        35989      50  417.302705  0.790359  0.001389   
7   K0M  109857        84399     111  979.728851  0.768262  0.001315   
8   K0G   62002        47898      89  556.465280  0.772523  0.001858   
15  K1Z     799          698       1    8.115390  0.873592  0.001433   

                                             geometry  pop_count  
2   MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...   17911.61  
6   MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   35934.75  
7   MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   48236.25  
8   MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   35465.14  
15  MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...   23618.08

In [34]:
scaled = detector.scale()

In [35]:
scaled.head()

id      bids  impressions    clicks     spend  Win Rate       CTR  \
2   K1B -0.383247    -0.384259 -0.389365 -0.384493  1.494445 -0.471010   
6   K0J  1.455018     1.481477  1.473339  1.481083 -0.631492  0.042970   
7   K0M  4.065998     4.007778  3.745839  4.012177 -0.922464  0.015587   
8   K0G  2.123452     2.102955  2.926249  2.107358 -0.866355  0.216516   
15  K1Z -0.360921    -0.360201 -0.352111 -0.360389  0.464515  0.059251   

                                             geometry  pop_count  
2   MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...  -0.501546  
6   MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   0.446636  
7   MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808  
8   MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   0.421931  
15  MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...  -0.201333

In [36]:
detector.create_model(contamination = 0.1)

IsolationForest(contamination=0.1)

In [37]:
detector.model.get_params()

{'bootstrap': False,
 'contamination': 0.1,
 'max_features': 1.0,
 'max_samples': 'auto',
 'n_estimators': 100,
 'n_jobs': None,
 'random_state': None,
 'verbose': 0,
 'warm_start': False}

In [38]:
predictions = detector.predict()

In [39]:
predictions.head()

id      bids  impressions    clicks     spend  Win Rate       CTR  \
2   K1B -0.383247    -0.384259 -0.389365 -0.384493  1.494445 -0.471010   
6   K0J  1.455018     1.481477  1.473339  1.481083 -0.631492  0.042970   
7   K0M  4.065998     4.007778  3.745839  4.012177 -0.922464  0.015587   
8   K0G  2.123452     2.102955  2.926249  2.107358 -0.866355  0.216516   
15  K1Z -0.360921    -0.360201 -0.352111 -0.360389  0.464515  0.059251   

                                             geometry  pop_count  score  \
2   MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...  -0.501546      1   
6   MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   0.446636      1   
7   MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808      1   
8   MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   0.421931      1   
15  MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...  -0.201333      1   

    anomaly  
2     False  
6     False  
7     False  
8     False  
15    False

In [40]:
detector.graph_scatter()

In [41]:
detector.graph_geo()

In [42]:
from recipes.categorical_anomaly import CategoricalAnomalyDetector
lof = CategoricalAnomalyDetector(ont, 
                        metrics_column=['impressions', 'clicks','CTR', 'pop_count'], 
                        category_column='id', model_type='LocalOutlierFactor',
                        geotif_path='earth_pop/GHS_POP_E2015_GLOBE_R2019A_4326_30ss_V1_0.tif',ScalerClass="StandardScaler")

In [43]:
lof.raster_to_vector()

id    bids  impressions  clicks       spend  Win Rate       CTR  \
2    K1B     249          237       0    2.759268  0.951807  0.000000   
6    K0J   45535        35989      50  417.302705  0.790359  0.001389   
7    K0M  109857        84399     111  979.728851  0.768262  0.001315   
8    K0G   62002        47898      89  556.465280  0.772523  0.001858   
15   K1Z     799          698       1    8.115390  0.873592  0.001433   
..   ...     ...          ...     ...         ...       ...       ...   
582  P3C    1178          955       0   11.126938  0.810696  0.000000   
584  P0V    3497         2730       4   31.574477  0.780669  0.001465   
585  P0T   36093        28817      48  334.297858  0.798410  0.001666   
587  P0E    3841         2754       1   32.041069  0.717001  0.000363   
588  P0R    8587         6938      10   80.727584  0.807966  0.001441   

                                              geometry  pop_count  
2    MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...   17911.61  
6    MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   35934.75  
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   48236.25  
8    MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   35465.14  
15   MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...   23618.08  
..                                                 ...        ...  
582  MULTIPOLYGON (((-80.99643 46.49092, -80.99821 ...   16216.31  
584  MULTIPOLYGON (((-94.37484 49.72693, -94.37316 ...   17216.64  
585  MULTIPOLYGON (((-90.84559 48.24667, -90.87558 ...   29009.14  
587  MULTIPOLYGON (((-79.34665 44.91020, -79.33064 ...    2741.76  
588  MULTIPOLYGON (((-84.07389 46.33472, -84.07115 ...   11508.17  

[496 rows x 9 columns]

In [44]:
lof.scale()

id      bids  impressions    clicks     spend  Win Rate       CTR  \
2    K1B -0.383247    -0.384259 -0.389365 -0.384493  1.494445 -0.471010   
6    K0J  1.455018     1.481477  1.473339  1.481083 -0.631492  0.042970   
7    K0M  4.065998     4.007778  3.745839  4.012177 -0.922464  0.015587   
8    K0G  2.123452     2.102955  2.926249  2.107358 -0.866355  0.216516   
15   K1Z -0.360921    -0.360201 -0.352111 -0.360389  0.464515  0.059251   
..   ...       ...          ...       ...       ...       ...       ...   
582  P3C -0.345537    -0.346790 -0.389365 -0.346836 -0.363696 -0.471010   
584  P0V -0.251403    -0.254160 -0.240349 -0.254815 -0.759089  0.071092   
585  P0T  1.071745     1.107203  1.398831  1.107535 -0.525477  0.145469   
587  P0E -0.237440    -0.252908 -0.352111 -0.252716 -1.597465 -0.336687   
588  P0R -0.044788    -0.034564 -0.016824 -0.033611 -0.399644  0.062211   

                                              geometry  pop_count  
2    MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...  -0.501546  
6    MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   0.446636  
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808  
8    MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   0.421931  
15   MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...  -0.201333  
..                                                 ...        ...  
582  MULTIPOLYGON (((-80.99643 46.49092, -80.99821 ...  -0.590734  
584  MULTIPOLYGON (((-94.37484 49.72693, -94.37316 ...  -0.538108  
585  MULTIPOLYGON (((-90.84559 48.24667, -90.87558 ...   0.082286  
587  MULTIPOLYGON (((-79.34665 44.91020, -79.33064 ...  -1.299619  
588  MULTIPOLYGON (((-84.07389 46.33472, -84.07115 ...  -0.838426  

[496 rows x 9 columns]

In [45]:
lof.create_model(n_neighbors = 48, contamination = 0.08)

LocalOutlierFactor(contamination=0.08, n_neighbors=48)

In [46]:
lof.predict()

id      bids  impressions    clicks     spend  Win Rate       CTR  \
2    K1B -0.383247    -0.384259 -0.389365 -0.384493  1.494445 -0.471010   
6    K0J  1.455018     1.481477  1.473339  1.481083 -0.631492  0.042970   
7    K0M  4.065998     4.007778  3.745839  4.012177 -0.922464  0.015587   
8    K0G  2.123452     2.102955  2.926249  2.107358 -0.866355  0.216516   
15   K1Z -0.360921    -0.360201 -0.352111 -0.360389  0.464515  0.059251   
..   ...       ...          ...       ...       ...       ...       ...   
582  P3C -0.345537    -0.346790 -0.389365 -0.346836 -0.363696 -0.471010   
584  P0V -0.251403    -0.254160 -0.240349 -0.254815 -0.759089  0.071092   
585  P0T  1.071745     1.107203  1.398831  1.107535 -0.525477  0.145469   
587  P0E -0.237440    -0.252908 -0.352111 -0.252716 -1.597465 -0.336687   
588  P0R -0.044788    -0.034564 -0.016824 -0.033611 -0.399644  0.062211   

                                              geometry  pop_count  score  \
2    MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...  -0.501546      1   
6    MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   0.446636      1   
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808     -1   
8    MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   0.421931      1   
15   MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...  -0.201333      1   
..                                                 ...        ...    ...   
582  MULTIPOLYGON (((-80.99643 46.49092, -80.99821 ...  -0.590734      1   
584  MULTIPOLYGON (((-94.37484 49.72693, -94.37316 ...  -0.538108      1   
585  MULTIPOLYGON (((-90.84559 48.24667, -90.87558 ...   0.082286      1   
587  MULTIPOLYGON (((-79.34665 44.91020, -79.33064 ...  -1.299619      1   
588  MULTIPOLYGON (((-84.07389 46.33472, -84.07115 ...  -0.838426      1   

     anomaly  
2      False  
6      False  
7       True  
8      False  
15     False  
..       ...  
582    False  
584    False  
585    False  
587    False  
588    False  

[496 rows x 11 columns]

In [47]:
lof.graph_scatter()

In [48]:
lof.graph_highd()

In [49]:
lof.graph_highd(three_d = True)

In [50]:
from recipes.categorical_anomaly import CategoricalAnomalyDetector
loda = CategoricalAnomalyDetector(ont, 
                        metrics_column=['impressions', 'clicks', 'CTR', 'pop_count'], 
                        category_column='id', model_type='LODA',
                        geotif_path='earth_pop/GHS_POP_E2015_GLOBE_R2019A_4326_30ss_V1_0.tif',ScalerClass="StandardScaler")

In [51]:
loda.raster_to_vector()

id    bids  impressions  clicks       spend  Win Rate       CTR  \
2    K1B     249          237       0    2.759268  0.951807  0.000000   
6    K0J   45535        35989      50  417.302705  0.790359  0.001389   
7    K0M  109857        84399     111  979.728851  0.768262  0.001315   
8    K0G   62002        47898      89  556.465280  0.772523  0.001858   
15   K1Z     799          698       1    8.115390  0.873592  0.001433   
..   ...     ...          ...     ...         ...       ...       ...   
582  P3C    1178          955       0   11.126938  0.810696  0.000000   
584  P0V    3497         2730       4   31.574477  0.780669  0.001465   
585  P0T   36093        28817      48  334.297858  0.798410  0.001666   
587  P0E    3841         2754       1   32.041069  0.717001  0.000363   
588  P0R    8587         6938      10   80.727584  0.807966  0.001441   

                                              geometry  pop_count  
2    MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...   17911.61  
6    MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   35934.75  
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   48236.25  
8    MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   35465.14  
15   MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...   23618.08  
..                                                 ...        ...  
582  MULTIPOLYGON (((-80.99643 46.49092, -80.99821 ...   16216.31  
584  MULTIPOLYGON (((-94.37484 49.72693, -94.37316 ...   17216.64  
585  MULTIPOLYGON (((-90.84559 48.24667, -90.87558 ...   29009.14  
587  MULTIPOLYGON (((-79.34665 44.91020, -79.33064 ...    2741.76  
588  MULTIPOLYGON (((-84.07389 46.33472, -84.07115 ...   11508.17  

[496 rows x 9 columns]

In [52]:
loda.scale()

id      bids  impressions    clicks     spend  Win Rate       CTR  \
2    K1B -0.383247    -0.384259 -0.389365 -0.384493  1.494445 -0.471010   
6    K0J  1.455018     1.481477  1.473339  1.481083 -0.631492  0.042970   
7    K0M  4.065998     4.007778  3.745839  4.012177 -0.922464  0.015587   
8    K0G  2.123452     2.102955  2.926249  2.107358 -0.866355  0.216516   
15   K1Z -0.360921    -0.360201 -0.352111 -0.360389  0.464515  0.059251   
..   ...       ...          ...       ...       ...       ...       ...   
582  P3C -0.345537    -0.346790 -0.389365 -0.346836 -0.363696 -0.471010   
584  P0V -0.251403    -0.254160 -0.240349 -0.254815 -0.759089  0.071092   
585  P0T  1.071745     1.107203  1.398831  1.107535 -0.525477  0.145469   
587  P0E -0.237440    -0.252908 -0.352111 -0.252716 -1.597465 -0.336687   
588  P0R -0.044788    -0.034564 -0.016824 -0.033611 -0.399644  0.062211   

                                              geometry  pop_count  
2    MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...  -0.501546  
6    MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   0.446636  
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808  
8    MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   0.421931  
15   MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...  -0.201333  
..                                                 ...        ...  
582  MULTIPOLYGON (((-80.99643 46.49092, -80.99821 ...  -0.590734  
584  MULTIPOLYGON (((-94.37484 49.72693, -94.37316 ...  -0.538108  
585  MULTIPOLYGON (((-90.84559 48.24667, -90.87558 ...   0.082286  
587  MULTIPOLYGON (((-79.34665 44.91020, -79.33064 ...  -1.299619  
588  MULTIPOLYGON (((-84.07389 46.33472, -84.07115 ...  -0.838426  

[496 rows x 9 columns]

In [53]:
loda.create_model()

LODA()

In [54]:
loda.predict()

id      bids  impressions    clicks     spend  Win Rate       CTR  \
2    K1B -0.383247    -0.384259 -0.389365 -0.384493  1.494445 -0.471010   
6    K0J  1.455018     1.481477  1.473339  1.481083 -0.631492  0.042970   
7    K0M  4.065998     4.007778  3.745839  4.012177 -0.922464  0.015587   
8    K0G  2.123452     2.102955  2.926249  2.107358 -0.866355  0.216516   
15   K1Z -0.360921    -0.360201 -0.352111 -0.360389  0.464515  0.059251   
..   ...       ...          ...       ...       ...       ...       ...   
582  P3C -0.345537    -0.346790 -0.389365 -0.346836 -0.363696 -0.471010   
584  P0V -0.251403    -0.254160 -0.240349 -0.254815 -0.759089  0.071092   
585  P0T  1.071745     1.107203  1.398831  1.107535 -0.525477  0.145469   
587  P0E -0.237440    -0.252908 -0.352111 -0.252716 -1.597465 -0.336687   
588  P0R -0.044788    -0.034564 -0.016824 -0.033611 -0.399644  0.062211   

                                              geometry  pop_count  score  \
2    MULTIPOLYGON (((-75.54520 45.43477, -75.55599 ...  -0.501546      1   
6    MULTIPOLYGON (((-77.93027 45.37394, -78.17846 ...   0.446636      1   
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808     -1   
8    MULTIPOLYGON (((-76.05783 44.89132, -76.05972 ...   0.421931      1   
15   MULTIPOLYGON (((-75.74219 45.39723, -75.75374 ...  -0.201333      1   
..                                                 ...        ...    ...   
582  MULTIPOLYGON (((-80.99643 46.49092, -80.99821 ...  -0.590734      1   
584  MULTIPOLYGON (((-94.37484 49.72693, -94.37316 ...  -0.538108      1   
585  MULTIPOLYGON (((-90.84559 48.24667, -90.87558 ...   0.082286      1   
587  MULTIPOLYGON (((-79.34665 44.91020, -79.33064 ...  -1.299619      1   
588  MULTIPOLYGON (((-84.07389 46.33472, -84.07115 ...  -0.838426      1   

     anomaly  
2      False  
6      False  
7       True  
8      False  
15     False  
..       ...  
582    False  
584    False  
585    False  
587    False  
588    False  

[496 rows x 11 columns]

In [55]:
loda.get_anomalies()

id      bids  impressions    clicks     spend  Win Rate        CTR  \
7    K0M  4.065998     4.007778  3.745839  4.012177 -0.922464   0.015587   
28   K0A  7.935260     7.852127  7.508502  7.865449 -0.894469   0.025208   
29   K0H  3.331196     3.294297  3.373298  3.293713 -0.888728   0.057401   
30   K0L  6.560438     6.588351  6.092847  6.592152 -0.750319   0.010036   
46   K0K  4.829500     4.832830  5.534035  4.834254 -0.783305   0.116237   
71   K0C  2.544232     2.611868  2.702724  2.613516 -0.549008   0.061841   
121  L0R  2.542568     2.487718  2.143913  2.499059 -0.976189  -0.015866   
146  L4C -0.255787    -0.239079 -0.389365 -0.238549  0.691412  -0.471010   
149  K9J  4.150633     4.226070  3.894855  4.215210 -0.618824   0.009296   
181  K6K -0.393192    -0.396522 -0.389365 -0.396806 -4.454921  -0.471010   
204  L9T  6.842596     6.721580  6.986945  6.705850 -0.962916   0.066282   
210  L6Z -0.234760    -0.214760 -0.389365 -0.214846  0.706765  -0.471010   
238  L6M  3.154781     3.009939  3.261536  3.004872 -1.204929   0.084414   
276  L5M -0.297557    -0.289229 -0.314857 -0.288632  0.443999  -0.111335   
278  L5N  4.174055     3.998123  3.261536  3.986881 -1.183452  -0.040288   
314  N0B  4.136832     4.081359  3.149773  4.085392 -0.914273  -0.061380   
315  N0G  4.000036     4.136832  4.416413  4.138019 -0.469698   0.078493   
338  N0M  3.596548     3.568845  4.267396  3.570986 -0.858968   0.137699   
353  M5C -0.392949    -0.396157 -0.389365 -0.396440  0.812254  -0.471010   
356  M5H -0.391650    -0.394748 -0.389365 -0.395017  0.247915  -0.471010   
383  N0H  4.391021     4.345940  4.639937  4.351056 -0.885752   0.078493   
437  N3C  4.910197     5.282930  2.628216  5.289259 -0.070077  -0.195703   
502  P6A  2.827079     2.916213  4.304650  2.907426 -0.502354   0.263511   
542  P7J -0.393274    -0.396522 -0.389365 -0.396802  2.129047  -0.471010   
554  P3N -0.391528    -0.394800 -0.352111 -0.395057 -0.797158  10.101272   

                                              geometry  pop_count  score  \
7    MULTIPOLYGON (((-78.91076 44.21080, -78.91731 ...   1.093808     -1   
28   MULTIPOLYGON (((-75.38381 45.34085, -75.39819 ...   4.701013     -1   
29   MULTIPOLYGON (((-76.95872 44.07585, -76.96484 ...   1.093589     -1   
30   MULTIPOLYGON (((-78.64111 44.31767, -78.64686 ...   2.492820     -1   
46   MULTIPOLYGON (((-76.61657 43.92247, -76.60763 ...   4.353308     -1   
71   MULTIPOLYGON (((-75.44425 45.04771, -75.40857 ...   1.339687     -1   
121  MULTIPOLYGON (((-79.90484 43.37897, -79.98498 ...   3.483156     -1   
146  MULTIPOLYGON (((-79.44286 43.89595, -79.44360 ...   2.774258     -1   
149  MULTIPOLYGON (((-78.39220 44.37315, -78.38709 ...   0.889049     -1   
181  MULTIPOLYGON (((-74.70840 45.08554, -74.76944 ...  -1.309924     -1   
204  MULTIPOLYGON (((-79.88511 43.57331, -79.87888 ...   3.140046     -1   
210  MULTIPOLYGON (((-79.78292 43.73792, -79.80324 ...   0.751939     -1   
238  MULTIPOLYGON (((-79.72396 43.52486, -79.72692 ...   2.243956     -1   
276  MULTIPOLYGON (((-79.73003 43.52965, -79.74557 ...   4.284942     -1   
278  MULTIPOLYGON (((-79.73752 43.63289, -79.73604 ...   3.585882     -1   
314  MULTIPOLYGON (((-80.03204 43.78158, -79.96904 ...   2.957229     -1   
315  MULTIPOLYGON (((-81.61024 44.31586, -81.59768 ...   3.122748     -1   
338  MULTIPOLYGON (((-81.92651 43.22683, -81.85745 ...   2.066132     -1   
353  MULTIPOLYGON (((-79.37575 43.64745, -79.37145 ...  -1.443861     -1   
356  MULTIPOLYGON (((-79.38403 43.64496, -79.37696 ...  -1.443861     -1   
383  MULTIPOLYGON (((-80.51101 44.59569, -80.49366 ...   0.954063     -1   
437  MULTIPOLYGON (((-80.29126 43.44096, -80.30564 ...   0.086239     -1   
502  MULTIPOLYGON (((-84.55675 46.50385, -84.54264 ...   0.229611     -1   
542  MULTIPOLYGON (((-89.27949 48.35992, -89.28793 ...  -1.195412     -1   
554  MULTIPOLYGON (((-80.94459 46.63858, -81.02073 ...  -0.879129     -1   

     anomaly  
7       True  
28      True  
29     

In [56]:
loda.graph_scatter()

In [57]:
len(loda.get_anomalies())

25

In [58]:
loda.graph_highd()